In [87]:
# Code for creation of Figures 5-9 and Table 1 in "Packed voters and cracked voters"
# August 02, 2018
# Gregory S. Warrington

%matplotlib inline 
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.geometry import Polygon
import matplotlib.pyplot as plt

import math

homepath = '/home/gswarrin/research/gerrymander/dilution/'
atlas_path = homepath + 'redistrict-atlas/'
census_path = homepath + shapefiles/'

fips_st_dict = {'01':'AL','02':'AK','04':'AZ','05':'AR','06':'CA','08':'CO','09':'CT','10':'DE',\
                '11':'DC','12':'FL','13':'GA','15':'HI','16':'ID','17':'IL','18':'IN','19':'IA',\
                '20':'KS','21':'KY','22':'LA','23':'ME','24':'MD','25':'MA','26':'MI','27':'MN',\
                '28':'MS','29':'MO','30':'MT','31':'NE','32':'NV','33':'NH','34':'NJ','35':'NM',\
                '36':'NY','37':'NC','38':'ND','39':'OH','40':'OK','41':'OR','42':'PA','44':'RI',\
                '45':'SC','46':'SD','47':'TN','48':'TX','49':'UT','50':'VT','51':'VA','53':'WA',\
                '54':'WV','55':'WI','56':'WY'}
# switch roles of keys and pairs for dictionary so we can look up fips for state
st_fips_dict = {y:x for x,y in fips_st_dict.items()}


In [1]:
# code for creating overlays of district plans

def rewrite_PVI(x):
    """ rewrite PVI as a number
    """
    return 0.50 + x/100
    # print(x)
    # if x[0] == 'R':
    #     return 0.50 - float(x[2:])/100
    # else:
    #     return 0.50 + float(x[2:])/100
    
def explode(gdf):
    """ 
    Explodes a geodataframe; obtained from online forum
    
    Will explode muti-part geometries into single geometries. Original index is
    stored in column level_0 and zero-based count of geometries per multi-
    geometry is stored in level_1
    
    Args:
        gdf (gpd.GeoDataFrame) : input geodataframe with multi-geometries
        
    Returns:
        gdf (gpd.GeoDataFrame) : exploded geodataframe with a new index 
                                 and two new columns: level_0 and level_1
        
    """
    gs = gdf.explode()
    gdf2 = gs.reset_index().rename(columns={0: 'geometry'})
    gdf_out = gdf2.merge(gdf.drop('geometry', axis=1), left_on='level_0', right_index=True)
    gdf_out = gdf_out.set_index(['level_0', 'level_1']).set_geometry('geometry')
    gdf_out.crs = gdf.crs
    return gdf_out    

def spatial_overlays(df1, df2):
    """Compute overlay intersection of two 
        GeoPandasDataFrames df1 and df2; obtained from online forum
    """
    
    # Spatial Index to create intersections
    spatial_index = df2.sindex
    df1['bbox'] = df1.geometry.apply(lambda x: x.bounds)
    df1['histreg']=df1.bbox.apply(lambda x:list(spatial_index.intersection(x)))
    pairs = df1['histreg'].to_dict()
    nei = []
    for i,j in pairs.items():
        for k in j:
            nei.append([i,k])
    
    pairs = gpd.GeoDataFrame(nei, columns=['idx1','idx2'], crs=df1.crs)
    pairs = pairs.merge(df1, left_on='idx1', right_index=True)
    pairs = pairs.merge(df2, left_on='idx2', right_index=True, suffixes=['_1','_2'])
    pairs['Intersection'] = pairs.apply(lambda x: (x['geometry_1'].intersection(x['geometry_2'])).buffer(0), axis=1)
    pairs = gpd.GeoDataFrame(pairs, columns=pairs.columns, crs=df1.crs)
    cols = pairs.columns.tolist()
    cols.remove('geometry_1')
    cols.remove('geometry_2')
    cols.remove('histreg')
    cols.remove('bbox')
    cols.remove('Intersection')
    dfinter = pairs[cols+['Intersection']].copy()
    dfinter.rename(columns={'Intersection':'geometry'}, inplace=True)
    dfinter = gpd.GeoDataFrame(dfinter, columns=dfinter.columns, crs=pairs.crs)
    dfinter = dfinter.loc[dfinter.geometry.is_empty==False]
    del df1['bbox']
    del df1['histreg']
    return dfinter

def form_intersections(dfA, dfB, dfC):
    """ Form intersections of plans. fnA and fnB assumed to be from Atlas. 
        fnC from census
    """
    dA = explode(dfA)
    dB = explode(dfB)
    dC = explode(dfC)

    dA = dA.reset_index(level=[0,1])
    dB = dB.reset_index(level=[0,1])
    dC = dC.reset_index(level=[0,1])

    dAB = spatial_overlays(dA,dB)
    dAB = explode(dAB)
    dAB = dAB.reset_index(level=[0,1])

    del dAB['level_0']
    del dAB['level_1']

    # one intersection
    dAC = spatial_overlays(dA,dC)
    dAC = explode(dAC)
    dAC = dAC.reset_index(level=[0,1])

    del dAC['level_0']
    del dAC['level_1']

    # another intersection
    dBC = spatial_overlays(dB,dC)
    dBC = explode(dBC)
    dBC = dBC.reset_index(level=[0,1])

    del dBC['level_0']
    del dBC['level_1']
    
    for dD in [dAC, dBC, dAB]:
        del dD['idx1']
        del dD['idx2']
        del dD['level_0_1']
        del dD['level_1_1']
        del dD['level_0_2']
        del dD['level_1_2']
        del dD['STATE_2']
        dD.rename(columns={'STATE_1':'STATE'}, inplace=True)
        
    # triple intersection
    dABC = spatial_overlays(dC,dAB)
    
    del dABC['idx1']
    del dABC['idx2']
    del dABC['level_0']
    del dABC['level_1']
    del dABC['STATE_2']
    dABC.rename(columns={'STATE_1':'STATE','PVI':'PVI_3','DISTRICT':'DISTRICT_3','distid':'distid_3'}, inplace=True)
    
    return dA, dB, dC, dAB, dAC, dBC, dABC

def get_three_plans(curst,fnA,fnB,fnC,pvidf,cenpvidf):
    dfA = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnA + '.shp') # first precursor plan
    dfB = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnB + '.shp') # second precursor plan
    dfC = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnC + '.shp') # second precursor plan
    dfA['distid'] = dfA['STATE'] + '-' + dfA['MAPTYPE'] + '-' + dfA['DISTRICT']
    dfA = dfA.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    dfB['distid'] = dfB['STATE'] + '-' + dfB['MAPTYPE'] + '-' + dfB['DISTRICT']
    dfB = dfB.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    dfC['distid'] = dfC['STATE'] + '-' + dfC['MAPTYPE'] + '-' + dfC['DISTRICT']
    dfC = dfC.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
        
    return dfA, dfB, dfC

def get_census_plans(curst,fnA,fnB,fnC,pvidf,cenpvidf):
    dfA = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnA + '.shp') # first precursor plan
    dfB = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnB + '.shp') # second precursor plan
    dfA['distid'] = dfA['STATE'] + '-' + dfA['MAPTYPE'] + '-' + dfA['DISTRICT']
    dfA = dfA.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    dfB['distid'] = dfB['STATE'] + '-' + dfB['MAPTYPE'] + '-' + dfB['DISTRICT']
    dfB = dfB.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
        
    dfC = gpd.read_file(census_path + fnC + '.shp') # current plan
    dfC = dfC[dfC['STATEFP'] == st_fips_dict[curst]]
    dfC['STATEFP'] = dfC.STATEFP.apply(lambda x: fips_st_dict[x])
    dfC.rename(index=str,columns={'CD115FP': 'DISTRICT', 'STATEFP': 'STATE'},inplace=True)
    dfC = dfC.join(cenpvidf.set_index(['STATE','DISTRICT']),how='left',on=['STATE','DISTRICT'])
    dfC = dfC[['STATE','DISTRICT','geometry','PVI']]   
    
    # dfA['geometry'] = dfA.simplify(0.01)
    # dfB['geometry'] = dfB.simplify(0.01)
    # dfC['geometry'] = dfC.simplify(0.01)
    return dfA, dfB, dfC

def new_get_census_plans(curst,fnA,fnB,fnC,pvidf,cenpvidf):
    """ pull current plan from atlas as well
    """
    dfA = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnA + '.shp') # first precursor plan
    dfB = gpd.read_file(atlas_path + 'shp/' + curst + '-' + fnB + '.shp') # second precursor plan
    dfC = gpd.read_file(atlas_path + 'shp/' + curst + '-' + 'current' + '.shp') # second precursor plan
    dfA['distid'] = dfA['STATE'] + '-' + dfA['MAPTYPE'] + '-' + dfA['DISTRICT']
    dfA = dfA.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    dfB['distid'] = dfB['STATE'] + '-' + dfB['MAPTYPE'] + '-' + dfB['DISTRICT']
    dfB = dfB.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    dfC['distid'] = dfC['STATE'] + '-' + dfC['MAPTYPE'] + '-' + dfC['DISTRICT']
    dfC = dfC.join(pvidf[['distid','PVI']].set_index('distid'),how='left',on='distid')
    
    ############# for obtained "current" plan from census source
    # dfC = gpd.read_file(census_path + fnC + '.shp') # current plan
    # dfC = dfC[dfC['STATEFP'] == st_fips_dict[curst]]
    # dfC['STATEFP'] = dfC.STATEFP.apply(lambda x: fips_st_dict[x])
    # dfC.rename(index=str,columns={'CD115FP': 'DISTRICT', 'STATEFP': 'STATE'},inplace=True)
    # dfC = dfC.join(cenpvidf.set_index(['STATE','DISTRICT']),how='left',on=['STATE','DISTRICT'])
    # dfC = dfC[['STATE','DISTRICT','geometry','PVI']]   
    
    return dfA, dfB, dfC

def get_pvis():
    """ Read in partisan lean of districts. 0.5 is even; > 0.5 is Democratic 
    """
    # PVI that came with Atlas plans
    pvidf = pd.read_csv(atlas_path + 'newdistricts.csv')
    pvidf = pvidf[['distid','state','PVI']]
    pvidf.rename(index=str,columns={'state':'STATE'},inplace=True)
    pvidf['PVI'] = pvidf.PVI.apply(lambda x: 0.50 + x/100)

    # PVI from Cook; only used if current plan is from census source
    cenpvidf = pd.read_csv(homepath + '2017PVI.csv',sep='\t',\
                           header=None,names=['STATE','DISTRICT','PVI'],index_col=False,\
                           dtype={'STATE':str, 'DISTRICT': str, 'PVI':float})
    cenpvidf['PVI'] = cenpvidf.PVI.apply(lambda x: 0.5 + x/100)

    return pvidf, cenpvidf

def is_packed(row,isDem=True,mindiff=0):
    """ Returns true if voters packed relative to two plans.
    PVI_2 is for the "current" plan; mindiff is minimum difference in values
    """
    if (isDem & ((row['PVI_2'] - mindiff) > row['PVI_1'] > 0.5)):
        return 1
    elif ((not isDem) & ((row['PVI_2'] + mindiff) < row['PVI_1'] < 0.5)):
        return 1
    else:
        return 0

def is_cracked(row,isDem=True,mindiff=0):
    """ Returns true if voters cracked relative to two plans.
    PVI_2 is for the "current" plan; mindiff is minimum difference in values
    """
    if (isDem & (row['PVI_2'] < 0.5) & (row['PVI_1'] > 0.5) & (abs(row['PVI_2']-row['PVI_1']) >= mindiff)):
        return 1
    elif ((not isDem) & (row['PVI_2'] > 0.5) & (row['PVI_1'] < 0.5) & \
          (abs(row['PVI_2']-row['PVI_1']) >= mindiff)):
        return 1
    else:
        return 0

def pandc_pair(df,mindiff=0):
    """ label regions as packed or cracked
    """
    for i,row in df.iterrows():
        df.loc[i,'Dpacked'] = is_packed(row,True,mindiff)
        df.loc[i,'Dcracked'] = is_cracked(row,True,mindiff)   
        df.loc[i,'Rpacked'] = is_packed(row,False,mindiff)
        df.loc[i,'Rcracked'] = is_cracked(row,False,mindiff)   

def make_pics(curst):
    """ Plot partisan lean of each district; not sure if fully working.
    """
    vals = np.linspace(0,1,256)
    np.random.shuffle(vals)
    cmap = plt.cm.colors.ListedColormap(plt.cm.jet(vals))
    strs = [curst + x for x in ['-A','-B','-C','-AB','-AC','-BC','-ABC']]
    for i,df in enumerate([dA,dB,dC,dAB,dAC,dBC,dABC]):
        fig = plt.figure(figsize=(10,10))
        if i < 3:
            df.plot('PVI',edgecolor='black',cmap='seismic_r',vmin=0,vmax=1)
        plt.savefig(homepath + strs[i],dpi=1000)
        plt.close()
        # df.to_file(homepath + strs[i] + '.shp')
        print(("Done %s" % (strs[i])))
           
def new_make_double(curst,dA,dB,dC,dAC,dBC,isDem):
    """ Make picture showing packed/cracked regions for two precursor
    plans relative to one final plan
    """
    axes = [0 for x in range(5)]
    axes[0] = plt.subplot2grid((6,4), (0,0), colspan=2, rowspan=2)
    axes[1] = plt.subplot2grid((6,4), (0,2), colspan=2, rowspan = 2)
    axes[2] = plt.subplot2grid((6,4), (2,0), colspan=2, rowspan = 2)
    axes[3] = plt.subplot2grid((6,4), (2,2), colspan=2, rowspan = 2)
    axes[4] = plt.subplot2grid((6,4), (4,1), colspan=2, rowspan = 2)
    fig = axes[0].figure
    
    # f, axes = plt.subplots(3,2, figsize=(8,6),sharey=True)
    # axes = axes.ravel()
    for ax in axes:
        ax.set_aspect('equal')
        ax.axis('off')
        
    # If want title for each plot
    # axes[0].set_title(dA.loc[0,'MAPTYPE'])
    # axes[1].set_title(dB.loc[0,'MAPTYPE'])
    # axes[2].set_title('Packed and cracked regions')
    # axes[3].set_title('Packed and cracked regions')
    # axes[4].set_title('Current map')
    # axes[5].set_title('Current map')
    
    if isDem:
        packedstr = 'Dpacked'
        crackedstr = 'Dcracked'
    else:
        packedstr = 'Rpacked'
        crackedstr = 'Rcracked'
        
    # work on first triple
    packed = dAC[dAC[packedstr]==1]
    cracked = dAC[dAC[crackedstr]==1]
    dA.plot('PVI',ax=axes[0],edgecolor='black',cmap='seismic_r',vmin=0,vmax=1)
    dC.plot('PVI',ax=axes[4],edgecolor='black',cmap='seismic_r',vmin=0,vmax=1)
    packed.plot(ax=axes[4],facecolor='none',edgecolor='gray',linewidth=0.5)
    cracked.plot(ax=axes[4],facecolor='none',edgecolor='gray',linewidth=0.5)
    dAC.plot(ax=axes[2],edgecolor='gray',facecolor='white',linewidth=0.5)
    packed.plot(ax=axes[2],edgecolor='gray',facecolor='purple',linewidth=0.5)
    cracked.plot(ax=axes[2],edgecolor='gray',facecolor='orange',linewidth=0.5)
    
    # work on second triple
    packedB = dBC[dBC[packedstr]==1]
    # print(packedB)
    crackedB = dBC[dBC[crackedstr]==1]
    dB.plot('PVI',ax=axes[1],edgecolor='black',cmap='seismic_r',vmin=0,vmax=1)
    # dC.plot('PVI',ax=axes[5],edgecolor='black',cmap='seismic_r',vmin=0,vmax=1)
    # packedB.plot(ax=axes[5],facecolor='none',edgecolor='gray',linewidth=0.5)
    #crackedB.plot(ax=axes[5],facecolor='none',edgecolor='gray',linewidth=0.5)
    dBC.plot(ax=axes[3],edgecolor='gray',facecolor='white',linewidth=0.5)
    if len(packedB) > 0:
        packedB.plot(ax=axes[3],edgecolor='gray',facecolor='purple',linewidth=0.5)
    if len(crackedB) > 0:
        crackedB.plot(ax=axes[3],edgecolor='gray',facecolor='orange',linewidth=0.5)

    axes[0].text(0.07,.9,'A',transform=fig.transFigure,fontsize=12, fontweight='bold')
    axes[1].text(0.55,.9,'B',transform=fig.transFigure,fontsize=12, fontweight='bold')
    axes[2].text(0.07,.58,'C',transform=fig.transFigure,fontsize=12, fontweight='bold')
    axes[3].text(0.55,.58,'D',transform=fig.transFigure,fontsize=12, fontweight='bold')
    axes[4].text(0.31,.26,'E',transform=fig.transFigure,fontsize=12, fontweight='bold')

    plt.tight_layout()
    
    plt.savefig(homepath + curst + '-new-five',dpi=1000)
    plt.close()



In [138]:
# Figure 5

# reading in files to get intersected district plans
# illustrate location of packed and cracked voters with respect ot three plans

pvidf, cenpvidf = get_pvis()
dfA, dfB, dfC = get_census_plans('MD','Competitive', 'Dem', 'cb_2016_us_cd115_5m',pvidf, cenpvidf)
# dfA, dfB, dfC = get_three_plans('VA','Competitive', 'Compact', 'Dem', pvidf, cenpvidf)
dA, dB, dC, dAB, dAC, dBC, dABC = form_intersections(dfA, dfB, dfC)

pandc_pair(dAC)
pandc_pair(dAB)
pandc_pair(dBC)

# Make picture for paper
new_make_double('MD',dA,dB,dC,dAC,dBC,False)

# shows how Atlas PVI values are stored (once converted)
# pvidf.head()

In [126]:
# Common functions needed for WI and NC


# wipath contains the git files from Herschlag et al.
wipath = homepath + 'duke/WIRedistrictingData/'

# For adding data about partisan support to shapefile
wishape = 'WI-election-data/2012_2020_Election_Data_with_2017_Wards.shp'

# check for equal populations
def check_pop_dev(df):
    """ look at population deviations
    """
    ser = df.groupby('District')['PERSONS'].sum()
    mydev = (ser.max()-ser.min())*1.0/ser.mean()
    return mydev < 0.05

# using the column given by "distrstr", compute Dem support within each district
def compute_district_averages(df,diststr,demstr,repstr):
    """ Compute Democratic support within district
    """
    ndf = df.groupby(diststr)[[demstr,repstr]].sum()
    ndf['PVI'] = ndf[demstr]*1.0/(ndf[demstr]+ndf[repstr])
    return ndf

def update_wards(df):
    """ Update which wards have packed/cracked voters relative to this comparator plan
    """
    for i,row in df.iterrows():
        df.loc[i,'TotDPacked'] += df.loc[i,'Dpacked']
        df.loc[i,'TotDCracked'] += df.loc[i,'Dcracked']
        df.loc[i,'TotRPacked'] += df.loc[i,'Rpacked']
        df.loc[i,'TotRCracked'] += df.loc[i,'Rcracked']

def make_bins(x,nbins,tot):
    """ for display
    """
    # don't want a separate value of 1; that would add an extra bin
    # if x == tot and x > 0:
    #     print(x)
    #     x -= 1
    tmp = x*nbins*1.0/tot
    return math.floor(tmp)*1.0/nbins

def make_geoid(row):
    """ Split out wards for which geoid couldn't be obtained by straight concatenation
    """
    # bdf is the shape file. we want to know which adf codes not found there.
    # 061: DUPLIN, CYCK - adf lists as CYCK rather than CYRK found in bdf
    # 165: SCOTLAND, we have 01,...,09. bdf wants no leading 0
    # 177: TYRRELL, we have 1,2,3 bdf wants a leading 0
    # 185: WARREN, we have 001,...,014 bdf wants no leading 0s at all.
    if row['StateCode'] == "37" and len(row['vtd']) <= 4:
        if row['CountyCode'] == "061" and row['vtd'] == "CYCK":
            return row['StateCode'] + row['CountyCode'] + "CYRK"
        elif row['CountyCode'] == "165" and int(row['vtd']) < 10:
            return row['StateCode'] + row['CountyCode'] + ("%1d" % (int(row['vtd'])))
        elif row['CountyCode'] == "177" and int(row['vtd']) < 10:
            return row['StateCode'] + row['CountyCode'] + ("%02d" % (int(row['vtd'])))
        elif row['CountyCode'] == "185" and int(row['vtd']) <= 14:
            return row['StateCode'] + row['CountyCode'] + ("%d" % (int(row['vtd'])))
    return row['StateCode'] + row['CountyCode'] + row['vtd']

def find_max_dem_col(row):
    return max(row['PDP'],row['PDC'])

def find_max_rep_col(row):
    return max(row['PRP'],row['PRC'])

def find_max_all_col(row):
    return max([row['PDP'],row['PDC'],row['PRP'],row['PRC']])


In [192]:
# Figures 8,9; Table 1
# Generates shapefile for two Wisconsin pictures in paper

# This has 6895 wards under OBJECTID_1 or OBJECTID
# OBJECTID_1 and OBJECTID are always the same
# DEM and REP can be used to compute averate party support
erdf = pd.read_csv(wipath + 'VotingData/electionResults-fixed.csv')
erdf = erdf[['OBJECTID','GEOID','PERSONS','ASMSIM','PREDEM16','PREREP16','USSDEM16','USSREP16',\
             'GOVDEM14','GOVREP14','SOSDEM14','SOSREP14','TRSDEM14','TRSREP14','USSDEM14','USSREP14']]
erdf['DEM'] = erdf['PREDEM16'] + erdf['USSDEM16'] + erdf['GOVDEM14'] + erdf['SOSDEM14'] + \
                erdf['TRSDEM14'] + erdf['USSDEM14']
erdf['REP'] = erdf['PREREP16'] + erdf['USSREP16'] + erdf['GOVREP14'] + erdf['SOSREP14'] + \
                erdf['TRSREP14'] + erdf['USSREP14']

# This maps CombinedWards to Wards, but doesn't list in a way that's easy for us to work with.
# We want a dataframe that has Wards as index and CombinedWards as values
# Assumes no CombinedWard is made from more than 3 Wards
wmdf = pd.read_csv(wipath + 'CombinedWardsToWards.txt',header=None,sep='\t',\
                  names=['CWard','Ward1','Ward2','Ward3'])

invdf = erdf[['OBJECTID']].rename(columns={'OBJECTID':'Ward'})   # these are all of the wards
invdf = invdf.set_index('Ward')
invdf['CombinedWard'] = None
for i,row in wmdf.iterrows():
    if not math.isnan(row['Ward1']):
        invdf.loc[row['Ward1'],'CombinedWard'] = row['CWard']-1
    if not math.isnan(row['Ward2']):
        invdf.loc[row['Ward2'],'CombinedWard'] = row['CWard']-1
    if not math.isnan(row['Ward3']):
        invdf.loc[row['Ward3'],'CombinedWard'] = row['CWard']-1
erdf = erdf.join(invdf,how='left',on='OBJECTID')

# Compute Dem support in "current" (enacted) plan
# ASMSIM is a modified version of ASM (which I guess left some wards unassigned to districts)
curdf = compute_district_averages(erdf,'ASMSIM','DEM','REP')
curdf.rename(columns={'PVI': 'PVI_2'},inplace=True)
del curdf['DEM']
del curdf['REP']
# this will place same PVI on all wards within a given district
erdf = erdf.join(curdf,how='left',on='ASMSIM')

# Run through simulated plans and mark off packed/cracked
wi_adf = erdf
NumSims = 100
mindiff = 0.05
wi_adf['TotDPacked'] = 0
wi_adf['TotDCracked'] = 0
wi_adf['TotRPacked'] = 0
wi_adf['TotRCracked'] = 0
for i in range(NumSims):
    j = 17*i+23
    wi_plandf = pd.read_csv(wipath + 'ensembleOfDistricts/districtmaps/districtMap' + str(j) + '.txt',sep='\t',\
                    header=None,names=['CombinedWard','District'],dtype={'CombinedWard':int,'District':int})
    # not necessary; handled by combinedward code
    # plandf.FID = test_plandf.FID.apply(lambda x: x+1)
    
    wi_adf = wi_adf.join(wi_plandf.set_index('CombinedWard'),how='left',on='CombinedWard')
    wi_simdf = compute_district_averages(wi_adf,'District','DEM','REP')
    del wi_simdf['DEM']
    del wi_simdf['REP']

    wi_simdf.rename(columns={'PVI': 'PVI_1'},inplace=True)
    wi_adf = wi_adf.join(wi_simdf,how='left',on='District')

    pandc_pair(wi_adf,mindiff)
    update_wards(wi_adf)
    if i%10 == 0:
        print("Done with %i" % (i))
    del wi_adf['District']
    del wi_adf['PVI_1']
    
wi_adf['PDP'] = wi_adf['TotDPacked'].apply(make_bins,args = (5,NumSims))
wi_adf['PDC'] = wi_adf['TotDCracked'].apply(make_bins,args = (5,NumSims))
wi_adf['PRP'] = wi_adf['TotRPacked'].apply(make_bins,args = (5,NumSims))
wi_adf['PRC'] = wi_adf['TotRCracked'].apply(make_bins,args = (5,NumSims))

wi_alldf = gpd.read_file(homepath + wishape)

wi_alldf = wi_alldf.join(wi_adf.set_index('GEOID'),how='left',on='GEOID',lsuffix='LL',rsuffix='RR')

# This is the shapefile that can be pulled into QGis
wi_alldf.to_file(homepath + 'WI-100-six-diff05-aug02.shp')

# let's keep track of max time packed/cracked for each district
wi_cdf = pd.DataFrame()
for t in ['PDP','PDC','PRP','PRC']:
    wi_bdf = wi_adf.groupby('ASMSIM')[t].max()
    wi_cdf = wi_cdf.join(pd.DataFrame(wi_bdf.value_counts()),how='outer')
wi_cdf = wi_cdf.sort_index()
wi_cdf


Done with 0
Done with 10
Done with 20
Done with 30
Done with 40
Done with 50
Done with 60
Done with 70
Done with 80
Done with 90


PDP  PDC   PRP   PRC
0.0  74.0   67  66.0  82.0
0.2   6.0    4  19.0   4.0
0.4   4.0    5   8.0   4.0
0.6   6.0    9   4.0   2.0
0.8   9.0   12   2.0   7.0
1.0   NaN    2   NaN   NaN

In [171]:
# Figures 6,7
# Create NC pictures in paper. Very similar code to WI. Inputs are a little different.

# This is folder containing git repository from Herschlag et al.
ncpath = homepath + 'duke/districtingDataRepository/'

##########################
# read in election results
# VTD, congresional districts, and lists of votes for various races
elecdf = pd.read_csv(homepath + 'duke/NC_2012.tab',sep='\t')
# which races to use to compute partisan lean of each district
racelist = ['USP','GOV','AGR','TRE','SOS']
vlist = []
for x in racelist:
    for y in ['_dv','_rv','_tv']:
        vlist.append(('g2012_' + x + y))
vlist = ['county','vtd','cd'] + vlist
elecdf = elecdf[vlist]

elecdf['DEM'] = 0
elecdf['REP'] = 0
for x in filter(lambda x: x[-2:] == 'dv', vlist):
    elecdf['DEM'] = elecdf['DEM'] + elecdf[x]
for x in filter(lambda x: x[-2:] == 'rv', vlist):
    elecdf['REP'] = elecdf['REP'] + elecdf[x]

###########################
# read in county codes
county_df = pd.read_csv(homepath + 'duke/st37_nc_cou.txt',header=None,\
                        names=['State','StateCode','CountyCode','CountyName','blah'],\
                        converters={'CountyCode': lambda x: str(x), 'StateCode': lambda x: str(x)})
county_df['County'] = county_df['CountyName'].apply(lambda x: x.upper())
county_df = county_df[['County','StateCode','CountyCode']]
elecdf = elecdf.join(county_df.set_index('County'),how='left',on='county')
for i,row in elecdf.iterrows():
    elecdf.loc[i,'GEOID10'] = make_geoid(row)
    
fidf = pd.read_csv(ncpath + 'preprocessedData/arcgis_FIDtovtdkeymap.txt',sep='\t')
fidf = fidf.set_index('GEOID10')

elecdf = elecdf.join(fidf,how='left',on='GEOID10')

# Compute Dem support in "current" (enacted) plan
# using 'cd' here instead of 'ASMSIM'
tmpdf = compute_district_averages(elecdf,'cd','DEM','REP')
tmpdf.rename(columns={'PVI': 'PVI_2'},inplace=True)
del tmpdf['DEM']
del tmpdf['REP']
# this will place same PVI on all wards within a given district
elecdf = elecdf.join(tmpdf,how='left',on='cd')

adf = elecdf
NumSims = 1000
mindiff = 0.05
adf['TotDPacked'] = 0
adf['TotDCracked'] = 0
adf['TotRPacked'] = 0
adf['TotRCracked'] = 0
for i in range(NumSims):
    j = 17*i+23
    jstr = "%05d" % (j)
    # print(jstr)
    plandf = pd.read_csv(ncpath + 'districtMaps/districtMap' + jstr + '.txt',sep='\t',\
                    header=None,names=['FID','District'],dtype={'FID':int,'District':int})
    # the indices in districtMap????? files start at 0
    plandf.FID = plandf.FID.apply(lambda x: x+1)

    adf = adf.join(plandf.set_index('FID'),how='left',on='FID')
    simdf = compute_district_averages(adf,'District','DEM','REP')
    del simdf['DEM']
    del simdf['REP']

    simdf.rename(columns={'PVI': 'PVI_1'},inplace=True)
    adf = adf.join(simdf,how='left',on='District')

    pandc_pair(adf,mindiff)
    update_wards(adf)
    if i%50 == 0:
        print("Done with %i" % (i))
    del adf['District']
    del adf['PVI_1']
    
# Add data about partisan support to shapefile
# From this file we only use the geometry information of each VTD
ncshape = 'tl_2012_37_vtd10.shp'

adf['PDP'] = adf['TotDPacked'].apply(make_bins,args = (5,NumSims))
adf['PDC'] = adf['TotDCracked'].apply(make_bins,args = (5,NumSims))
adf['PRP'] = adf['TotRPacked'].apply(make_bins,args = (5,NumSims))
adf['PRC'] = adf['TotRCracked'].apply(make_bins,args = (5,NumSims))

alldf = gpd.read_file(homepath + '/duke/' + ncshape)

alldf = alldf.join(adf.set_index('GEOID10'),how='left',on='GEOID10',lsuffix='LL',rsuffix='RR')

alldf.to_file(homepath + 'NC-1000-six-diff05-aug02.shp')


Done with 0
Done with 50
Done with 100
Done with 150
Done with 200
Done with 250
Done with 300
Done with 350
Done with 400
Done with 450
Done with 500
Done with 550
Done with 600
Done with 650
Done with 700
Done with 750
Done with 800
Done with 850
Done with 900
Done with 950


In [73]:
# to create enacted-district borders

argdf = alldf.dissolve('cd')
argdf.reset_index().to_file(homepath + 'dis-NCnew-100-six-jul31.shp')

In [191]:
# let's keep track of max time packed/cracked for each district
cdf = pd.DataFrame()
cadf = adf
for t in ['PDP','PDC','PRP','PRC']:
    bdf = adf.groupby('cd')[t].max()
    cdf = cdf.join(pd.DataFrame(bdf.value_counts()),how='outer')
cdf = cdf.sort_index().fillna(0)
cdf

PDP  PDC  PRP   PRC
0.0  10.0    4  8.0  10.0
0.2   0.0    1  4.0   1.0
0.4   0.0    1  0.0   0.0
0.6   0.0    1  0.0   0.0
0.8   3.0    6  1.0   2.0

In [2]:
# Misc code

# for checking regions with specific properties
# alldf[alldf['PRC'] > 0].plot()

# if we want to look at specific counties
# county_df[county_df['County'] == "WARREN"]

In [5]:
# for listing maximum frequencies by district and property

# xdf = adf
# for i,row in xdf.iterrows():
#     xdf.loc[i,'PCDem'] = find_max_dem_col(row)
#     xdf.loc[i,'PCRep'] = find_max_rep_col(row)
#     xdf.loc[i,'PCAll'] = find_max_all_col(row)
# ydf = pd.DataFrame()
# for t in ['PDP','PDC','PRP','PRC']: # ['PCDem','PCRep','PCAll']:
#     print(t)
#     # xdf[t]
#     ydf[t] = xdf.groupby('cd')[t].max()# .value_counts()
#     # print(ydf)
#     # print(t)
#     # cdf[t] = bdf.value_counts() # .sort_index()
# ydf = ydf.sort_index()
# ydf

In [3]:
# this was for finding geodid10's that weren't computed properly

othertypes = ['PROVISIONAL','ABSENTEE BY MAIL','ONE STOP','ACCUMULATED','TRANSFER','CURBSIDE']

# bdf is the shape file. we want to know which adf codes not found there.
# 061: DUPLIN, CYCK - adf lists as CYCK rather than CYRK found in bdf
# 165: SCOTLAND, we have 01,...,09. bdf wants no leading 0
# 177: TYRRELL, we have 1,2,3 bdf wants a leading 0
# 185: WARREN, we have 001,...,014 bdf wants no leading 0s at all.
# odf = adf[~adf.GEOID10.isin(bdf.GEOID10)]
# odf[~odf.vtd.isin(othertypes)]